# Import Libraries and setup Hugging Face

In [1]:
# Pace Setup
# !module load anaconda3
# !module load gcc/12.3.0
# !module load cuda/12.6.1

In [2]:
!nvidia-smi

import os

os.environ['PYTORCH_CUDA_ALLOC_CONF'] = 'expandable_segments:True'

import time
from dotenv import load_dotenv
import torch
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report
from tqdm import tqdm
from datasets import load_dataset
from prettytable import PrettyTable

# Update HF cache directory
env_path = os.path.abspath(os.path.join(os.getcwd(), '..', '.env'))
print(env_path)
load_dotenv(env_path)
hf_cache_dir = os.getenv('TRANSFORMERS_CACHE')
os.makedirs(hf_cache_dir, exist_ok=True)
print(f"Hugging Face cache directory set to: {hf_cache_dir}")

from transformers import AutoModelForCausalLM, AutoTokenizer

# Check cuda version torch is using
print(f"Using torch {torch.__version__} with cuda {torch.version.cuda}")

workspace_dir = os.getenv('WORKSPACE_DIR')

seed = 42

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")

Sat Dec  7 23:34:28 2024       
+-----------------------------------------------------------------------------------------+
| NVIDIA-SMI 555.42.02              Driver Version: 555.42.02      CUDA Version: 12.5     |
|-----------------------------------------+------------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id          Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |           Memory-Usage | GPU-Util  Compute M. |
|                                         |                        |               MIG M. |
|=========================================+========================+======================|
|   0  NVIDIA A100-PCIE-40GB          On  |   00000000:C1:00.0 Off |                    0 |
| N/A   35C    P0             43W /  250W |       1MiB /  40960MiB |      0%      Default |
|                                         |                        |             Disabled |
+-----------------------------------------+-----

/storage/ice1/3/5/jzwicker3/dl-fp/lib/python3.12/site-packages/transformers/utils/hub.py:128: FutureWarning: Using `TRANSFORMERS_CACHE` is deprecated and will be removed in v5 of Transformers. Use `HF_HOME` instead.
  warnings.warn(


Using torch 2.5.1 with cuda 12.4
Using device: cuda


# Import the dataset
It is stored in the dataset directory which is gitignored so run this block to repopulate if needed

In [3]:
# # Check if dataset is present
# dataset_dir = os.path.join(workspace_dir, 'datasets')
# os.makedirs(dataset_dir, exist_ok=True)

# if not os.path.exists(os.path.join(dataset_dir, 'IMDB Dataset.csv')):
#     !kaggle datasets download lakshmi25npathi/imdb-dataset-of-50k-movie-reviews --path {dataset_dir} --unzip

# # Load dataset into dataframe
# dataset = pd.read_csv(os.path.join(dataset_dir, 'IMDB Dataset.csv'))
# print(dataset.head())

# _, test_set = train_test_split(dataset, test_size=0.2, random_state=seed)

imdb = load_dataset("imdb")

test_dataset = imdb['test'].shuffle(seed=seed)#.select([i for i in list(range(500))])
train_dataset = imdb['train'].shuffle(seed=seed)

print(f"Train dataset: {len(train_dataset)}")
print(f"Test dataset: {len(test_dataset)}")
print(test_dataset[0])

Train dataset: 25000
Test dataset: 25000
{'text': "<br /><br />When I unsuspectedly rented A Thousand Acres, I thought I was in for an entertaining King Lear story and of course Michelle Pfeiffer was in it, so what could go wrong?<br /><br />Very quickly, however, I realized that this story was about A Thousand Other Things besides just Acres. I started crying and couldn't stop until long after the movie ended. Thank you Jane, Laura and Jocelyn, for bringing us such a wonderfully subtle and compassionate movie! Thank you cast, for being involved and portraying the characters with such depth and gentleness!<br /><br />I recognized the Angry sister; the Runaway sister and the sister in Denial. I recognized the Abusive Husband and why he was there and then the Father, oh oh the Father... all superbly played. I also recognized myself and this movie was an eye-opener, a relief, a chance to face my OWN truth and finally doing something about it. I truly hope A Thousand Acres has had the same

# Define Experiment Functions

In [4]:
"""
To calculate the values of accuracy, recall, specificity, precision, and F-score, you need the confusion matrix or the key components: True Positives (TP), True Negatives (TN), False Positives (FP), and False Negatives (FN). Here's how each metric is calculated:

1. **Accuracy**: The proportion of correctly classified instances (both positive and negative) out of all instances.
   \[
   \text{Accuracy} = \frac{TP + TN}{TP + TN + FP + FN}
   \]

2. **Recall (Sensitivity)**: The proportion of actual positives correctly identified.
   \[
   \text{Recall} = \frac{TP}{TP + FN}
   \]

3. **Specificity**: The proportion of actual negatives correctly identified.
   \[
   \text{Specificity} = \frac{TN}{TN + FP}
   \]

4. **Precision**: The proportion of predicted positives that are actually positive.
   \[
   \text{Precision} = \frac{TP}{TP + FP}
   \]

5. **F-score**: The harmonic mean of precision and recall, balancing the two.
   \[
   \text{F-Score} = 2 \cdot \frac{\text{Precision} \cdot \text{Recall}}{\text{Precision} + \text{Recall}}
   \]

"""


def evaluate_model_zero_shot(model, tokenizer, device, dataset, top_k=50):
    # Data preparation
    reviews = [example['text'] for example in dataset]
    true_labels = [example['label'] for example in dataset]  # 0 for negative, 1 for positive

    # Define the prompts
    prompts = [f"Movie Review: {review} \n Only Answer if this Movie Review is Positive or Negative:" for review in reviews]

    # Perform inference
    predictions = []
    inference_times = []

    for idx, example in tqdm(enumerate(dataset), total=len(dataset), desc="Processing", leave=True):
        # Tokenize the input
        inputs = tokenizer.encode(prompts[idx], return_tensors="pt").to(device)

        # Perform inference
        start_time = time.time()
        with torch.no_grad():
            outputs = model(inputs)
            logits = outputs.logits
        end_time = time.time()

        # Get the probabilities for the next token
        next_token_logits = logits[:, -1, :]  # Only consider the last token's logits
        probabilities = torch.softmax(next_token_logits, dim=-1)

        # Get the top k most likely tokens
        top_k_probs, top_k_indices = torch.topk(probabilities, top_k) # these are sorted in order of most likely to least likely

        # Decode the top k tokens
        top_k_tokens = [tokenizer.decode([token]) for token in top_k_indices[0]]

        # Extract the sentiment prediction from the top k tokens, if the model did not predict a sentiment, default to negative
        pred = -1
        for token in top_k_tokens:
            token_lower = token.strip().lower()
            if token_lower == 'positive':
                pred = 1
                break
            elif token_lower == 'negative':
                pred = 0
            
        if pred == -1:
            print(f"Could not predict sentiment for review: {reviews[idx]}")
            print(f"Top k tokens: {top_k_tokens}")
            pred = 0

        # If the model did not predict a sentiment, default to negative
        predictions.append(pred)
        
        inference_times.append(end_time - start_time)


    # Calculate confusion matrix    
    tn, fp, fn, tp = confusion_matrix(true_labels, predictions).ravel()

    # Calculate metrics
    accuracy = (tp + tn) / (tp + tn + fp + fn)
    recall = tp / (tp + fn) if (tp + fn) > 0 else 0
    specificity = tn / (tn + fp) if (tn + fp) > 0 else 0
    precision = tp / (tp + fp) if (tp + fp) > 0 else 0
    f_score = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0

    # Calculate total and average inference times
    total_inference_time = sum(inference_times)
    average_inference_time = total_inference_time / len(inference_times)

    return {
        "accuracy": accuracy,
        "recall": recall,
        "specificity": specificity,
        "precision": precision,
        "f_score": f_score,
        "total_inference_time": total_inference_time,
        "average_inference_time": average_inference_time
    }



def evaluate_model_few_shot(model, tokenizer, device, dataset, top_k=50):
    # Data preparation
    reviews = [example['text'] for example in dataset]
    true_labels = [example['label'] for example in dataset]  # 0 for negative, 1 for positive

    # Define the prompts
    # example_review = "This movie was an absolute masterpiece with stunning visuals and a gripping story!"
    # example_review_neg = "This movie was terrible and I hated it."
    # example_negative_review_2 = "I really think this movie is not that good. It was a waste of time."
    few_shot_rev_1 = "Movie Review: I loved this movie ! So good plot ! \n Only Answer if this Movie Review is Positive or Negative: Positive \n"
    few_shot_rev_2 = "Movie Review: I hated this, could be a lot better \n Only Answer if this Movie Review is Positive or Negative: Negative \n"
 
    prompts = [f"{few_shot_rev_1} {few_shot_rev_2} Movie Review: {review} \n Only Answer if this Movie Review is Positive or Negative:" for review in reviews]

    # Perform inference
    predictions = []
    inference_times = []

    for idx, example in tqdm(enumerate(dataset), total=len(dataset), desc="Processing", leave=True):
        # Tokenize the input
        inputs = tokenizer.encode(prompts[idx], return_tensors="pt").to(device)

        # Perform inference
        start_time = time.time()
        with torch.no_grad():
            outputs = model(inputs)
            logits = outputs.logits
        end_time = time.time()

        # Get the probabilities for the next token
        next_token_logits = logits[:, -1, :]  # Only consider the last token's logits
        probabilities = torch.softmax(next_token_logits, dim=-1)

        # Get the top k most likely tokens
        top_k_probs, top_k_indices = torch.topk(probabilities, top_k) # these are sorted in order of most likely to least likely

        # Decode the top k tokens
        top_k_tokens = [tokenizer.decode([token]) for token in top_k_indices[0]]

        # Extract the sentiment prediction from the top k tokens, if the model did not predict a sentiment, default to negative
        pred = -1
        for token in top_k_tokens:
            token_lower = token.strip().lower()
            if token_lower == 'positive':
                pred = 1
                break
            elif token_lower == 'negative':
                pred = 0
            
        if pred == -1:
            print(f"Could not predict sentiment for review: {reviews[idx]}")
            print(f"Top k tokens: {top_k_tokens}")
            pred = 0

        # If the model did not predict a sentiment, default to negative
        predictions.append(pred)
        
        inference_times.append(end_time - start_time)

    # Calculate confusion matrix    
    tn, fp, fn, tp = confusion_matrix(true_labels, predictions).ravel()

    # Calculate metrics
    accuracy = (tp + tn) / (tp + tn + fp + fn)
    recall = tp / (tp + fn) if (tp + fn) > 0 else 0
    specificity = tn / (tn + fp) if (tn + fp) > 0 else 0
    precision = tp / (tp + fp) if (tp + fp) > 0 else 0
    f_score = 2 * (precision * recall) / (precision + recall) if (precision + recall) > 0 else 0

    # Calculate total and average inference times
    total_inference_time = sum(inference_times)
    average_inference_time = total_inference_time / len(inference_times)

    return {
        "accuracy": accuracy,
        "recall": recall,
        "specificity": specificity,
        "precision": precision,
        "f_score": f_score,
        "total_inference_time": total_inference_time,
        "average_inference_time": average_inference_time
    }


def create_results_table(results_dict, model_name="Model Results"):
    """
    Creates a formatted table from the results dictionary.
    
    Parameters:
        results_dict (dict): Dictionary containing evaluation metrics.
        model_name (str): Name of the model being evaluated.
    
    Returns:
        str: Formatted table as a string.
    """
    # Initialize a PrettyTable
    table = PrettyTable()
    
    # Set the table title
    table.title = f"Results for {model_name}"
    
    # Add columns
    table.field_names = ["Metric", "Value"]
    
    # Add rows for each metric
    table.add_row(["Accuracy", f"{results_dict['accuracy']:.2f}"])
    table.add_row(["Recall (Sensitivity)", f"{results_dict['recall']:.2f}"])
    if "specificity" in results_dict:  # Specificity might not be included in some results
        table.add_row(["Specificity", f"{results_dict['specificity']:.2f}"])
    table.add_row(["Precision", f"{results_dict['precision']:.2f}"])
    table.add_row(["F-Score", f"{results_dict['f_score']:.2f}"])
    table.add_row(["Total Inference Time (s)", f"{results_dict['total_inference_time']:.2f}"])
    table.add_row(["Average Inference Time (s)", f"{results_dict['average_inference_time']:.2f}"])
    
    # Return the table as a string
    return table.get_string()

<>:1: SyntaxWarning: invalid escape sequence '\['
<>:1: SyntaxWarning: invalid escape sequence '\['
/scratch/1030276/ipykernel_2812946/2386449730.py:1: SyntaxWarning: invalid escape sequence '\['
  """


# SmolLM-135M


In [5]:
# Clears cuda from last run
# if device == "cuda":
#     torch.cuda.empty_cache()
#     torch.cuda.ipc_collect()
#     torch.cuda.reset_peak_memory_stats()

#FROM https://huggingface.co/HuggingFaceTB/SmolLM2-135M TODO: Dont forget to cite the model in report
checkpoint = "HuggingFaceTB/SmolLM2-135M"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)
model = AutoModelForCausalLM.from_pretrained(checkpoint).to(device)

## Zero Shot

In [6]:
zero_135_results = evaluate_model_zero_shot(model, tokenizer, device, test_dataset)

zero_135_table = create_results_table(zero_135_results, model_name="SmolLM2-135M Zero-Shot")
print(zero_135_table)

Processing:   0%|          | 16/25000 [00:08<1:51:30,  3.73it/s]

Could not predict sentiment for review: Don't pay any attention to the rave reviews of this film here. It is the worst Van Damme film and one of the worst of any sort I have ever seen. It would appeal to somebody with no depth whatever who requires nothing more than gunfire and explosions to be entertained.<br /><br />Seeing that this is directed by Peter Hyams it has made me realise that Peter has no talent as a director, but is very good at filming explosions and the like. However, movies need other elements as well; for example, a story. This one didn't have one. This might explain the awfulness of some of Mr. Hyams' more recent films, hardly any better than this one, really.<br /><br />One can't help wondering how some people ever were put behind a camera.
Top k tokens: [' <', ' ', ' I', ' It', ' This', '\n', ' The', ' Yes', '<', ' No', ' "', ' If', ' Don', ' You', ' A', ' yes', ' Not', ' Van', ' \n', '\n ', ' Good', ' There', ' it', '</', ' Y', ' (', ' In', 'This', ' Very', '\n  '

Processing:   0%|          | 41/25000 [00:08<21:24, 19.43it/s]  

Could not predict sentiment for review: This is just one of those films which cannot justify much of anything that happens. These people are going on a trek: the young girl wants to photograph animals. There really are no Piranhas, but I guess the psychotic hunter guy is the real piranha. Anyway, there are lots of animals and there is lots of driving. There is considerable anti-gun talk, but we all know where that is going. Toward the end, there's lots of action and a rape thrown in. Somebody must pay, and they do. It would have been nice to have a couple of piranhas to sort of fill the thing out. There were lots of monkeys. If you fast forward through the dull parts, you have a tight little five minutes.
Top k tokens: [' I', ' \n', ' This', ' Yes', ' ', '\n', ' It', ' The', ' If', ' No', ' There', ' You', ' Not', ' A', '\n ', ' Well', ' In', ' Very', ' We', ' Maybe', ' [', ' As', ' Y', ' "', ' yes', ' Some', ' My', ' At', ' Okay', ' Yeah', ' Probably', ' Absolutely', ' What', ' That',

Processing:   0%|          | 61/25000 [00:09<11:50, 35.08it/s]

...

Could not predict sentiment for review: There are lots of other comments here about how poor this film is. What I wanted to point out is how this film took the largest science project in history and made it look small. The Manhattan project was an incredible achievement and it was huge. Virtually all silver in the country went into making wire for electromagnetic separators. If there was every a choice between two alternative ways of doing things they just did both. The first sustained nuclear reactor was fired up under the stands of the University of Chicago football stadium with graduate students wielding axes as a scram mechanism. It's a fascinating story involving hundreds of locations and thousands of people that this film seems to reduce to a small group of eccentrics in New Mexico.<br /><br />The other thing I really disliked was the huge moral debate over if we should continue the project after Germany surrenders. Okay, we have thousands of (mostly) men who worked for years to 

Processing: 100%|█████████▉| 24986/25000 [09:27<00:00, 44.83it/s]

Could not predict sentiment for review: "Fat Girls" is among the worst films within the indie gay genre.<br /><br />The premise is promising: an average-looking gay teen is trapped in a repressive small TX town. His only kindred spirits are the other village HS misfits: the class 'fat girl', a naïve immigrant from Cuba, and the sensitive drama teacher. So far, interesting. In theory, this plot line creates a decent setup for an appealing coming of age story with a built-in audience---the thousands of gay men who grew up in small towns across America and experienced this adolescent anxiety first hand, peppered with a dose of self-deprecating humor.<br /><br />Unfortunately, rather than a nuanced dramedy, Ash Christian approaches his autobiographical subject matter with a poorly executed attempt at irony and dark humor. The result is a cast of unlikeable, derivative, two-dimensional characters which the viewer cannot but help feel indifferent toward. Sabrina (Fink) is a quasi-Goth bitter

Processing: 100%|██████████| 25000/25000 [09:28<00:00, 43.99it/s]

Could not predict sentiment for review: I went to see this film over Matchstick Men, in fact buying the tickets to Matchstick Men and going to the other, because it looked like a fun movie with action, romance, thrills, jungles, and exotic locations. They had all that but so do a lot of movies with a conception of story.<br /><br />All I can say is WHY WHY WHY WHY did they not just make it a straight narrative instead of some sappy flashback story.<br /><br />Here is all the movies from what I've seen the film was derived from: Of course, Indiana Jones and Romancing the Stone, but also True Lies, Proof of Life, that old 80s Tom Selleck movie, Bananas (Woody Allen), and Hero (from the use of digital extras).<br /><br />PS the only scene in the movie that was cool is when the central character finds her room blown up.
Top k tokens: [' I', ' <', ' ', ' The', '<', '\n', ' It', ' Yes', ' This', ' If', ' \n', '\n ', ' No', ' "', ' A', '\n  ', ' My', ' You', '</', ' http', ' </', ' yes', ' Y'

## Few Shot

In [7]:
few_135_results = evaluate_model_few_shot(model, tokenizer, device, test_dataset)

few_135_table = create_results_table(few_135_results, model_name="SmolLM2-135M Few-Shot")
print(few_135_table)

Processing: 100%|██████████| 25000/25000 [09:30<00:00, 43.82it/s]

+-------------------------------------+
|  Results for SmolLM2-135M Few-Shot  |
+----------------------------+--------+
|           Metric           | Value  |
+----------------------------+--------+
|          Accuracy          |  0.50  |
|    Recall (Sensitivity)    |  1.00  |
|        Specificity         |  0.00  |
|         Precision          |  0.50  |
|          F-Score           |  0.67  |
|  Total Inference Time (s)  | 468.77 |
| Average Inference Time (s) |  0.02  |
+----------------------------+--------+


# SmolLM-360M

In [8]:
# Clears cuda from last run
# if device == "cuda":
#     torch.cuda.empty_cache()
#     torch.cuda.ipc_collect()
#     torch.cuda.reset_peak_memory_stats()
    
checkpoint = "HuggingFaceTB/SmolLM2-360M"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)
model = AutoModelForCausalLM.from_pretrained(checkpoint).to(device)

## Zero Shot

In [ ]:
zero_360_results = evaluate_model_zero_shot(model, tokenizer, device, test_dataset)

zero_360_table = create_results_table(zero_360_results, model_name="SmolLM2-360M Zero-Shot")
print(zero_360_table)

Processing:   7%|▋         | 1858/25000 [00:54<10:57, 35.18it/s]

## Few Shot

In [ ]:
few_360_results = evaluate_model_few_shot(model, tokenizer, device, test_dataset)

few_360_table = create_results_table(few_360_results, model_name="SmolLM2-360M Few-Shot")
print(few_360_table)

# SmolLM2-1.7B

In [ ]:
# Clears cuda from last run
# if device == "cuda":
#     torch.cuda.empty_cache()
#     torch.cuda.ipc_collect()
#     torch.cuda.reset_peak_memory_stats()

checkpoint = "HuggingFaceTB/SmolLM2-1.7B"
tokenizer = AutoTokenizer.from_pretrained(checkpoint)
model = AutoModelForCausalLM.from_pretrained(checkpoint).to(device)

## Zero Shot

In [ ]:
zero_17_results = evaluate_model_zero_shot(model, tokenizer, device, test_dataset)

zero_17_table = create_results_table(zero_17_results, model_name="SmolLM2-1.7B Zero-Shot")
print(zero_17_table)

## Few Shot

In [ ]:
few_17_results = evaluate_model_few_shot(model, tokenizer, device, test_dataset)

few_17_table = create_results_table(few_17_results, model_name="SmolLM2-1.7B Few-Shot")
print(few_17_table)

# Print All Results

In [ ]:
print("All models evaluated successfully!")

results_dicts = [
    zero_135_results,
    few_135_results,
    zero_360_results,
    few_360_results,
    zero_17_results,
    few_17_results,
]

# List of model names
model_names = [
    "SmolLM2-135M Zero-Shot",
    "SmolLM2-135M Few-Shot",
    "SmolLM2-360M Zero-Shot",
    "SmolLM2-360M Few-Shot",
    "SmolLM2-1.7B Zero-Shot",
    "SmolLM2-1.7B Few-Shot",
]

table = PrettyTable()

# Define the columns
table.field_names = [
    "Model",
    "Accuracy",
    "Recall (Sensitivity)",
    "Specificity",
    "Precision",
    "F-Score",
    "Total Inference Time (s)",
    "Avg Inference Time (s)"
]

# Populate the table
for model_name, results in zip(model_names, results_dicts):
    table.add_row([
        model_name,
        f"{results['accuracy']:.2f}",
        f"{results['recall']:.2f}",
        f"{results['specificity']:.2f}",
        f"{results['precision']:.2f}",
        f"{results['f_score']:.2f}",
        f"{results['total_inference_time']:.2f}",
        f"{results['average_inference_time']:.2f}",
    ])

print(table)
print(results_dicts)

# Cleanup Cuda

In [ ]:
# Clears cuda from last run
# if device == "cuda":
#     torch.cuda.empty_cache()
#     torch.cuda.ipc_collect()
#     torch.cuda.reset_peak_memory_stats()